# Import Libraries

In [106]:
import numpy as np
import pandas as pd 
%matplotlib inline
import matplotlib.pyplot as plt
import seaborn as sea
import streamlit as str
import ydata_profiling

# Import Data file

In [107]:
df = pd.read_csv('class_customer_churn.csv')

# Exploring Data

In [108]:
df.head()

RowNumber  CustomerId   Surname  CreditScore Geography  Gender  Age  \
0          1    15634602  Hargrave          619    France  Female   42   
1          2    15647311      Hill          608     Spain  Female   41   
2          3    15619304      Onio          502    France  Female   42   
3          4    15701354      Boni          699    France  Female   39   
4          5    15737888  Mitchell          850     Spain  Female   43   

   Tenure    Balance  NumOfProducts  HasCrCard  IsActiveMember  \
0       2       0.00              1          1               1   
1       1   83807.86              1          0               1   
2       8  159660.80              3          1               0   
3       1       0.00              2          0               0   
4       2  125510.82              1          1               1   

   EstimatedSalary  Exited  
0        101348.88       1  
1        112542.58       0  
2        113931.57       1  
3         93826.63       0  
4         79084.10       0

In [109]:
nRow, nCol = df.shape
print(f'There are {nRow} rows and {nCol} columns')

There are 10000 rows and 14 columns


In [110]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 14 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   RowNumber        10000 non-null  int64  
 1   CustomerId       10000 non-null  int64  
 2   Surname          10000 non-null  object 
 3   CreditScore      10000 non-null  int64  
 4   Geography        10000 non-null  object 
 5   Gender           10000 non-null  object 
 6   Age              10000 non-null  int64  
 7   Tenure           10000 non-null  int64  
 8   Balance          10000 non-null  float64
 9   NumOfProducts    10000 non-null  int64  
 10  HasCrCard        10000 non-null  int64  
 11  IsActiveMember   10000 non-null  int64  
 12  EstimatedSalary  10000 non-null  float64
 13  Exited           10000 non-null  int64  
dtypes: float64(2), int64(9), object(3)
memory usage: 1.1+ MB


In [111]:
df.duplicated().sum()

np.int64(0)

In [112]:
from ydata_profiling import ProfileReport  
profile = ProfileReport(df)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 14/14 [00:00<00:00, 285.71it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [113]:
df.columns

Index(['RowNumber', 'CustomerId', 'Surname', 'CreditScore', 'Geography',
       'Gender', 'Age', 'Tenure', 'Balance', 'NumOfProducts', 'HasCrCard',
       'IsActiveMember', 'EstimatedSalary', 'Exited'],
      dtype='object')

# Feature Engineering and Data Preprocessing

In [114]:
df = df.drop(columns=["RowNumber", "CustomerId", "Surname"])

In [115]:
from sklearn.preprocessing import OneHotEncoder, RobustScaler , StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC 
from sklearn.metrics import classification_report, roc_auc_score , r2_score

In [116]:
numeric_features = ["CreditScore", "Age", "Tenure", "Balance", "NumOfProducts", "EstimatedSalary"]
categorical_features = ["Geography", "Gender"]
binary_features = ["HasCrCard", "IsActiveMember"]

In [117]:
x = df.drop(columns=["Exited"])
y = df["Exited"]

In [118]:
preprocessor = ColumnTransformer(
    transformers=[
        ("num", RobustScaler(), numeric_features),
        ("cat", OneHotEncoder(drop="first", handle_unknown="ignore"), categorical_features),
        ("bin", "passthrough", binary_features)
    ]
)

In [119]:
X_train, X_test, y_train, y_test = train_test_split( x, y, test_size=0.2,random_state=42,stratify=y )

# Building Model

In [120]:
LR = LogisticRegression()
RF = RandomForestClassifier()
SVM = SVC()

In [121]:
param1= {}
param1['classifier__max_iter'] = [1000]
param1['classifier__class_weight'] = ['balanced']
param1['classifier']= [LR]

param2= {}
param2['classifier__n_estimators'] = [100, 200, 300]
param2['classifier__max_depth'] = [5, 10, 15]
param2['classifier__class_weight'] = ['balanced']
param2['classifier__random_state'] = [42]
param2['classifier__n_jobs'] = [-1]
param2['classifier']= [RF]

param3= {}
param3['classifier__kernel'] = ["rbf"]
param3['classifier__C'] = [1.0 , 10.0, 100.0]
param3['classifier__gamma'] = ["scale"]
param3['classifier__class_weight'] = ["balanced"]
param3['classifier__probability'] = [True]
param3['classifier__random_state'] = [42]
param3['classifier']= [SVM]

In [122]:
pipeline = Pipeline(steps=[("preprocessor", preprocessor),("classifier", LR )])
params = [param1 , param2 , param3]

In [123]:
from sklearn.model_selection import GridSearchCV
gs =   GridSearchCV(pipeline, params, cv=5, scoring='roc_auc', n_jobs=-1, verbose=2)

In [124]:
gs.fit(X_train, y_train)

Fitting 5 folds for each of 13 candidates, totalling 65 fits


GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('preprocessor',
                                        ColumnTransformer(transformers=[('num',
                                                                         RobustScaler(),
                                                                         ['CreditScore',
                                                                          'Age',
                                                                          'Tenure',
                                                                          'Balance',
                                                                          'NumOfProducts',
                                                                          'EstimatedSalary']),
                                                                        ('cat',
                                                                         OneHotEncoder(drop='first',
                                                                                       handle_unknown='ignore'),
                                                                         ['Geography',
                                                                          'Gender']),
                                                                        ('bin',
                                                                         'passthrough',
                                                                         ['HasCrCard',
                                                                          'IsActiveMember'])])),
                                       ('classifier', Logisti...
                          'classifier__max_depth': [5, 10, 15],
                          'classifier__n_estimators': [100, 200, 300],
                          'classifier__n_jobs': [-1],
                          'classifier__random_state': [42]},
                         {'classifier': [SVC()],
                          'classifier__C': [1.0, 10.0, 100.0],
                          'classifier__class_weight': ['balanced'],
                          'classifier__gamma': ['scale'],
                          'classifier__kernel': ['rbf'],
                          'classifier__probability': [True],
                          'classifier__random_state': [42]}],
             scoring='roc_auc', verbose=2)

In [125]:
gs.best_params_

{'classifier': RandomForestClassifier(),
 'classifier__class_weight': 'balanced',
 'classifier__max_depth': 10,
 'classifier__n_estimators': 300,
 'classifier__n_jobs': -1,
 'classifier__random_state': 42}

In [126]:
gs.best_score_

np.float64(0.8611821132417102)

In [ ]:
import joblib
joblib.dump(gs.best_estimator_, "churn model.pkl")

['churn_model.pkl']

In [ ]:
Best_model = joblib.load("churn model.pkl")

In [129]:
y_pred = Best_model.predict(X_test)
print(classification_report(y_test, y_pred))
roc_auc = roc_auc_score(y_test, Best_model.predict_proba(X_test)[:,1])
print(f'ROC AUC Score: {roc_auc}')

              precision    recall  f1-score   support

           0       0.91      0.89      0.90      1593
           1       0.61      0.65      0.63       407

    accuracy                           0.84      2000
   macro avg       0.76      0.77      0.76      2000
weighted avg       0.85      0.84      0.85      2000

ROC AUC Score: 0.8640073046852708
